# Aggregate projections and error analysis

In [2]:
from oggm import cfg, workflow, utils, shop
import pandas as pd
import os, glob
import numpy as np
import xarray as xr
import seaborn as sns
import matplotlib.pyplot as plt
sns.set_style("whitegrid")

cfg.initialize()

import matplotlib
matplotlib.rcParams['figure.figsize'] = (14, 8)
import geopandas as gpd

2026-01-05 09:50:55: oggm.cfg: Reading default parameters from the OGGM `params.cfg` configuration file.
2026-01-05 09:50:55: oggm.cfg: Multiprocessing switched OFF according to the parameter file.
2026-01-05 09:50:55: oggm.cfg: Multiprocessing: using all available processors (N=32)
2026-01-05 09:50:55: oggm.utils: Checking the download verification file checksum...


In [40]:
len(pd_geodetic)

215547

In [2]:
pd_geodetic = utils.get_geodetic_mb_dataframe()[utils.get_geodetic_mb_dataframe().period=='2000-01-01_2020-01-01']
# ok, connectivity level 2 glaciers are not inside ...
rgis_05 = gpd.read_file(utils.get_rgi_region_file('05', version='62'))
rgis_05_remove = rgis_05.loc[(rgis_05['Connect'] ==2)].RGIId.values
assert len(np.intersect1d(pd_geodetic.index.values,rgis_05_remove)) == 0
total_area = pd_geodetic.area.sum()
total_counts = len(pd_geodetic)

# Get a list with the amount of failing glaciers and area for the different scenarios

In [8]:
scenarios = ['hist',  # same model (UKESM1.2-LL) being forced through the CMIP historical forcing
             'up2p0', # ramp-up phase
             'up2p0-gwl2p0',  # stabilisation at 2°C
             'up2p0-gwl2p0-50y-dn2p0', # "ramp-down" from 2C stabilisation after 50 years'
             'up2p0-gwl4p0',  # stabilisation at 4C
             "up2p0-gwl4p0-50y-dn2p0",  # "ramp-down" from 4C stabilisation after 50 years'
             #"piControl"  # same model with pre-industrial forcing'
            ]
bc = '_bc_1975_2014'
b_clim = 'w5e5'

pd_working = pd.DataFrame(index = pd_geodetic.index,
              columns=scenarios)
# we will set those that are not running afterwards to np.NaN value
pd_working.loc[pd_geodetic.index] = True
pd_working['area'] = pd_geodetic.area
pd_working['all_running_rgis'] = np.NaN
pd_working['rgi_reg'] = pd_geodetic.reg
for rgi_reg in np.arange(1,20,1): 
    print(rgi_reg)
    if rgi_reg < 10:
        rgi_reg_s = f'0{rgi_reg}'
    else:
        rgi_reg_s = rgi_reg
    dpath = f'/home/www/lschuster/terrafirma_oggm_proj/output_dir/RGI{rgi_reg_s}'
    # amount of glaciers in that rgi region
    rgi_reg_glaciers = pd_working.loc[pd_working.rgi_reg==int(rgi_reg)].index
    for scen in scenarios:  
        if scen == 'hist':
            opt = '_starting_at_1979_glacier_state_from_1975_sim_year_climate'
        else:
            opt = '_to_0_40_sim_year_starting_at_1979_glacier_state_from_0_sim_year_climate'
        #run_hydro_hc_era5_rgi62_gcm_from_2000_endyr2100_ISIMIP3b_mri-esm2-0_r1i1p1f1_ssp126_rgi01_7000_8000.nc
        with xr.open_mfdataset(f'{dpath}/run_terrafirma_UKESM1-2-LL_esm_{scen}{bc}{opt}_Batch_*.nc') as ds:
            ds = ds.volume.sel(time=1975).load()
        # make sure that all glaciers have been running
        assert len(ds.rgi_id.values) == len(rgi_reg_glaciers)
        rgis_error = list(set(rgi_reg_glaciers) - set(ds.dropna(dim='rgi_id').rgi_id.values))
        pd_working.loc[rgis_error, scen] = np.NaN
        ds.close()
all_running_rgis = pd_working[scenarios].dropna().index
pd_working.loc[all_running_rgis, 'all_running_rgis'] = True
all_running_rel = len(all_running_rgis)*100/len(pd_geodetic)
all_running_rel_area = pd_working.loc[all_running_rgis].area.sum()*100/pd_working.area.sum()
print(f'{b_clim}{bc}{opt}')
print(f'Amount of glaciers that run over the entire time period: {len(all_running_rgis)}')
print(f'Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: {all_running_rel:0.2f}%')
print(f'Relative percentage of glacier area where all gcms and ssp could run over the entire time period: {all_running_rel_area:0.2f}%')
#pd_rel_error_area_L5.to_csv('rel_error_area_statistics_for_oversh_stab_scenarios.csv')
pd_working.to_csv(f'working_rgis_for_oggm_v163_terrafirma_ukesm_bclim{bc}_rgi62.csv') #opt


1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19


/tmp/ipykernel_3702685/1437045573.py:42: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value 'True' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  pd_working.loc[all_running_rgis, 'all_running_rgis'] = True


w5e5_bc_1975_2014_to_0_40_sim_year_starting_at_1979_glacier_state_from_0_sim_year_climate
Amount of glaciers that run over the entire time period: 209846
Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: 97.36%
Relative percentage of glacier area where all gcms and ssp could run over the entire time period: 99.46%


In [27]:
for rgi_reg in np.arange(1,20,1): 
    if rgi_reg < 10:
        rgi_reg_s = f'0{rgi_reg}'
    else:
        rgi_reg_s = rgi_reg
    pd_working = pd.read_csv(f'working_rgis_for_oggm_v163_terrafirma_ukesm_bclim{bc}_rgi62.csv', index_col='rgiid')
    pd_working_sel = pd_working.loc[pd_working.rgi_reg==int(rgi_reg)]
    all_running_rgis_reg = pd_working_sel[scenarios].dropna().index
    all_running_rel_reg = len(all_running_rgis_reg)*100/len(pd_working_sel)
    all_running_rel_area_reg = pd_working.loc[all_running_rgis_reg].area.sum()*100/pd_working_sel.area.sum()
    print(rgi_reg)
    print(f'Amount of glaciers that run over the entire time period: {len(all_running_rgis_reg)}')
    assert all_running_rel_reg > 80
    assert all_running_rel_area_reg>90
    print(f'Relative percentage of glacier amount where all scenarios could run over the entire time period: {all_running_rel_reg:0.2f}%')
    print(f'Relative percentage of glacier area where all scenarios could run over the entire time period: {all_running_rel_area_reg:0.2f}%')

1
Amount of glaciers that run over the entire time period: 26989
Relative percentage of glacier amount where all scenarios could run over the entire time period: 99.56%
Relative percentage of glacier area where all scenarios could run over the entire time period: 99.98%
2
Amount of glaciers that run over the entire time period: 17295
Relative percentage of glacier amount where all scenarios could run over the entire time period: 91.73%
Relative percentage of glacier area where all scenarios could run over the entire time period: 99.48%
3
Amount of glaciers that run over the entire time period: 4483
Relative percentage of glacier amount where all scenarios could run over the entire time period: 98.40%
Relative percentage of glacier area where all scenarios could run over the entire time period: 99.84%
4
Amount of glaciers that run over the entire time period: 7276
Relative percentage of glacier amount where all scenarios could run over the entire time period: 98.13%
Relative percentage 

- in all regions minimum 90% of glacier area, and minimum 80% of glaciers did run for all scenarios (for all, except for RGI12, above 95% of area works)
- in total, globally 99.5% of glacier area works and 97.4% of glaciers

In [ ]:
pd_working = pd.read_csv(f'working_rgis_for_oggm_v163_terrafirma_ukesm_bclim{bc}_rgi62.csv', index_col='rgiid')
dfs = []
for scen in scenarios:  
    if scen == 'hist':
        opt = '_starting_at_1979_glacier_state_from_1975_sim_year_climate'
    else:
        opt = '_to_0_40_sim_year_starting_at_1979_glacier_state_from_0_sim_year_climate'
    df = []
    for rgi_reg in np.arange(1,20,1): 
        if rgi_reg < 10:
            rgi_reg_s = f'0{rgi_reg}'
        else:
            rgi_reg_s = rgi_reg
        dpath = f'/home/www/lschuster/terrafirma_oggm_proj/output_dir/RGI{rgi_reg_s}'
        rgi_reg_glaciers = pd_geodetic.loc[pd_geodetic.reg==int(rgi_reg)].index
        rgi_reg_glaciers_working = pd_working.loc[pd_working.rgi_reg == int(rgi_reg)]['all_running_rgis'].dropna().index.values
        #run_hydro_hc_era5_rgi62_gcm_from_2000_endyr2100_ISIMIP3b_mri-esm2-0_r1i1p1f1_ssp126_rgi01_7000_8000.nc
        with xr.open_mfdataset(f'{dpath}/run_terrafirma_UKESM1-2-LL_esm_{scen}{bc}{opt}_Batch_*.nc') as ds:
            ds = ds[['volume','volume_bsl','area']].sel(rgi_id=rgi_reg_glaciers_working).load().sum(dim='rgi_id')
            #ds_area = ds.area.sel(rgi_id=rgi_reg_glaciers_working).load().sum()
        ds = ds.reset_coords()
        ds = ds.drop_vars(['hydro_year','hydro_month','calendar_month', 'calendar_year'])
        ds.coords['rgi_reg'] = rgi_reg_s
        ds = ds.expand_dims('rgi_reg')
        df.append(ds)
    df = xr.concat(df, dim='rgi_reg', fill_value=np.NaN)
    df.coords['scenario'] = scen
    df.coords['gcm'] = 'terrafirma_ukesm'
    df.coords['n_all_running_rgis'] = len(pd_working.index.values)
    dfs.append(df)
    print(scen)
df_all_scenario = xr.concat(dfs, dim='scenario', fill_value=np.NaN)

### Compute SLE since 1975 and save it as additional variable 

In [63]:
ds_1975_volume_asl

array([1.91762740e+13, 1.10928108e+12, 2.61374953e+13, 8.92136115e+12,
       1.49684968e+13, 3.78715872e+12, 6.69398073e+12, 2.96313422e+11,
       1.23704946e+13, 1.36031232e+11, 1.24292473e+11, 5.10827397e+10,
       3.19209000e+12, 2.78125373e+12, 8.37448696e+11, 1.33278925e+11,
       5.54703834e+12, 7.36944538e+10, 3.27195579e+13], dtype=float32)

In [66]:
### similarly done as in Schuster et al. (2025): 
# http://localhost:7269/lab/tree/www_lschuster/provide/gfdl-esm2m_oversh_stab_uni_bern/B_main_analysis_figure_creation/2a_fig_2_suppl_prcp.ipynb
# sea level makes only sense globally probably
df_all_scenario['volume_asl']= df_all_scenario['volume']-df_all_scenario['volume_bsl']
# in 1975 (start of simluations), we just have one estimate, check this 
assert np.all(df_all_scenario.sel(time=1975).volume_asl.std(dim='scenario')/df_all_scenario.sel(time=1975).volume_asl.mean(dim='scenario')<0.001)
ds_1975_volume_asl = df_all_scenario.sel(time=1975).volume_asl.mean(dim='scenario')
# test when assuming that entire volume above sea level completely melts 
vol_asl_diff_1975 = ds_1975_volume_asl
# convert m3 into sea-level equivalent 
A_ocean = 3.625 * 10**8 * 1e6 # km2 --> 1e6
m_slr_all_1975_volume_lost = (vol_asl_diff_1975/A_ocean) *900/1028 # rhoice/rho_ocean
mm_slr_all_1975_volume_lost = m_slr_all_1975_volume_lost * 1000
### Farinotti et al 2019 states around 333mm in 2000, so around 336 in 1975 sounds reasonable... oK! 
# also note that this is the OGGM above sea-level estimates, thus can be different to the Farinotti et al. 2019 community estimate 
# (even if we would look at the same date, but here we also look at another date, i.e. 1975 and not the inventory year)
print(mm_slr_all_1975_volume_lost.sum().values)
## now compute slr from glacier melt from the various scenarios
# in 2500, volume asl depends on scenario
ds_volume_asl = df_all_scenario.volume_asl

vol_asl_diff = vol_asl_diff_1975 - ds_volume_asl
# convert m3 into sea-level equivalent 
m_slr = (vol_asl_diff/A_ocean) *900/1028 # rhoice/rho_ocean
mm_slr = m_slr * 1000
df_all_scenario['mm_slr_since_1975'] = mm_slr

335.84048


In [78]:
mm_slr_global_since_1975 = df_all_scenario['mm_slr_since_1975'].sum(dim='rgi_reg') 

In [81]:
assert np.all(mm_slr_global_since_1975 >-2)
# the total glacier slr contribution since 1975 should be less than if all glaciers melted away (assuming 1975 volume)
assert np.all(mm_slr_global_since_1975< mm_slr_all_1975_volume_lost.sum())

In [84]:
mm_slr_global_since_1975.max().values

array(310.04666138)

## Add some attributes to the netCDF file

In [107]:
df_all_scenario = df_all_scenario.drop_vars('volume_asl')

In [6]:
df_all_scenario.attrs['OGGM_version'] = 'oggm_v163'
df_all_scenario.attrs['RGI_version'] = 'rgiv62'

df_all_scenario.attrs['info'] = """Reanalysis dataset used for calibration: W5E5.
Bias correction period: 1975–2014, applied from W5E5 to up2p0 simulation years 0–39.
Simulations were initialized using the 1979 glacier state from the dynamical spinup
"""

df_all_scenario.attrs['time_validity'] = """All variables describe the state at the beginning of the given year.
For all "up2p0"-related scenarios, the time variable was shifted to start in 1975 instead of 1850, to match the adjusted climate period more realistically.
For the "hist"-scenario, we start in the original 1975 year. 
"""

df_all_scenario.attrs['rgi_reg_info'] = 'sum over all rgi_reg to get global estimates'
df_all_scenario.volume.attrs['unit'] = 'm3'
df_all_scenario.area.attrs['unit'] = 'm2'
df_all_scenario.mm_slr_since_1975.attrs['unit'] = 'mm sea-level rise since 1975 from glaciers'
df_all_scenario.volume_bsl.attrs['unit'] = 'm3' 
df_all_scenario.volume_bsl.attrs['info'] = 'Regional glacier volume below sea-level from all glaciers that did not fail for any of the scenarios  (>99.5% of global glacier area)'
df_all_scenario.volume.attrs['info'] = 'Regional total glacier volume from all glaciers that did not fail for any of the scenarios (>99.5% of global glacier area)'
df_all_scenario.area.attrs['info'] = 'Regional total glacier area from all glaciers that did not fail for any of the scenarios (>99.5% of global glacier area)'

df_all_scenario.mm_slr_since_1975.attrs['info'] = """
Sea-level rise contribution from glaciers.
Same approach as in Schuster et al. (2025).

Steps:
1. df_all_scenario['volume_asl'] = df_all_scenario['volume'] - df_all_scenario['volume_bsl']
2. ds_1975_volume_asl = df_all_scenario.sel(time=1975).volume_asl.mean(dim='scenario')
2. A_ocean = 3.625e8 * 1e6  # km² --> m²
3. vol_asl_diff = ds_1975_volume_asl - df_all_scenario['volume_asl']  # compute difference relative to 1975
4. m_slr = (vol_asl_diff / A_ocean) * 900 / 1028  # convert volume to m sea-level rise
5. mm_slr = m_slr * 1000  # convert meters to millimeters
"""


In [7]:
df_all_scenario

<xarray.Dataset> Size: 1MB
Dimensions:             (scenario: 6, rgi_reg: 19, time: 696)
Coordinates:
  * scenario            (scenario) <U22 528B 'hist' ... 'up2p0-gwl4p0-50y-dn2p0'
  * rgi_reg             (rgi_reg) <U2 152B '01' '02' '03' ... '17' '18' '19'
  * time                (time) float64 6kB 1.975e+03 1.976e+03 ... 2.67e+03
    gcm                 <U16 64B ...
    n_all_running_rgis  int64 8B ...
Data variables:
    volume              (scenario, rgi_reg, time) float32 317kB ...
    volume_bsl          (scenario, rgi_reg, time) float32 317kB ...
    area                (scenario, rgi_reg, time) float32 317kB ...
    mm_slr_since_1975   (rgi_reg, scenario, time) float32 317kB ...
Attributes:
    OGGM_version:   oggm_v163
    RGI_version:    rgiv62
    info:           Reanalysis dataset used for calibration: W5E5.\nBias corr...
    time_validity:  All variables describe the state at the beginning of the ...
    rgi_reg_info:   sum over all rgi_reg to get global estimates

In [8]:
df_all_scenario.to_netcdf(f'00c_regional_proj_common_running_terrafirma_ukesm{bc}_starting_at_1979_glacier_state_with_1975_similar_climate.nc')

In [87]:
df_all_scenario

<xarray.Dataset> Size: 2MB
Dimensions:             (scenario: 6, rgi_reg: 19, time: 696)
Coordinates:
  * scenario            (scenario) <U22 528B 'hist' ... 'up2p0-gwl4p0-50y-dn2p0'
  * rgi_reg             (rgi_reg) <U21 2kB '01' '02' '03' ... '17' '18' '19'
  * time                (time) float64 6kB 1.975e+03 1.976e+03 ... 2.67e+03
    gcm                 <U16 64B 'terrafirma_ukesm'
    n_all_running_rgis  int64 8B 215547
Data variables:
    volume              (scenario, rgi_reg, time) float32 317kB 2.01e+13 ... nan
    volume_bsl          (scenario, rgi_reg, time) float32 317kB 9.272e+11 ......
    area                (scenario, rgi_reg, time) float32 317kB 8.744e+10 ......
    volume_asl          (scenario, rgi_reg, time) float32 317kB 1.918e+13 ......
    mm_slr_since_1975   (rgi_reg, scenario, time) float32 317kB 0.0 ... nan